In [1]:
from utils import *

from pathlib import Path
import plotly.express as px
from plotly.subplots import make_subplots
import plotly.graph_objects as go

results_dir = Path("../results/at-400k")
scalars = TBScalars(".cache/at_400k")

In [2]:
dfs = []

for test_dir in results_dir.iterdir():
    with open(test_dir / "config.yml", "r") as f:
        cfg = yaml.load(f)

    assert cfg["env"]["type"] == "atari"
    env_id = cfg["env"]["atari"]["env_id"]
    seed = cfg["repro"]["seed"]

    df = scalars.read(test_dir)
    df = df[df["tag"] == "val/mean_ep_ret"].copy()
    df["env"] = env_id
    df["seed"] = seed
    env_id_, seed_eq, freq_eq = test_dir.name.split("-")
    df["freq"] = int(freq_eq.removeprefix("freq="))
    dfs.append(df)

df = pd.concat(dfs, axis=0)

env_ids = ["Pong", "CrazyClimber", "Assault"]
freqs = [64, 32, 16, 8, 4, 2, 1]

fig = make_subplots(
    rows=len(freqs),
    cols=len(env_ids),
    column_titles=env_ids,
    row_titles=freqs,
    horizontal_spacing=0.1,
    vertical_spacing=0.05,
)

for ix, env_id in enumerate(env_ids, 1):
    df1 = df[df["env"] == env_id]
    for iy, freq in enumerate(freqs, 1):
        df2 = df1[df1["freq"] == freq]
        xpr = px.line(df2, x="step", y="value", color="seed")
        for trace in xpr.data:
            fig.add_trace(trace, iy, ix)

fig.update_layout(
    showlegend=False,
    autosize=False,
    width=1024,
    height=480 * 3,
)

fig.write_image("../tex/assets/at_400k.perf.pdf")

fig

In [3]:
dfs = []

for test_dir in results_dir.iterdir():
    with open(test_dir / "config.yml", "r") as f:
        cfg = yaml.load(f)

    assert cfg["env"]["type"] == "atari"
    env_id = cfg["env"]["atari"]["env_id"]
    seed = cfg["repro"]["seed"]

    df = scalars.read(test_dir)
    df = df[df["tag"] == "wm/val_loss"].copy()
    df["env"] = env_id
    df["seed"] = seed
    env_id_, seed_eq, freq_eq = test_dir.name.split("=")
    df["freq"] = int(freq_eq.removeprefix("freq="))
    dfs.append(df)

df = pd.concat(dfs, axis=0)

env_ids = ["Pong", "CrazyClimber", "Assault"]
freqs = [64, 32, 16, 8, 4, 2]
seeds = [*range(3)]

fig = make_subplots(
    rows=len(freqs),
    cols=len(env_ids),
    column_titles=env_ids,
    row_titles=freqs,
    horizontal_spacing=0.1,
    vertical_spacing=0.05,
)


for ix, env_id in enumerate(env_ids, 1):
    df1 = df[df["env"] == env_id]
    for iy, freq in enumerate(freqs, 1):
        df2 = df1[df1["freq"] == freq]
        for seed in seeds:
            mask = df2["seed"] == seed
            df2.loc[mask, "value"] = exp_mov_avg(df2.loc[mask, "value"], 0.95)
        xpr = px.line(df2, x="step", y="value", color="seed")
        for trace in xpr.data:
            fig.add_trace(trace, row=iy, col=ix)
        fig.update_yaxes(type="log", row=iy, col=ix)

fig.update_layout(
    showlegend=False,
    autosize=False,
    width=1024,
    height=480 * 3,
)

fig.write_image("../tex/assets/at_400k.val_loss.pdf")

fig

In [5]:
env_ids = ["Pong", "CrazyClimber", "Assault"]

fig = make_subplots(
    rows=1,
    cols=len(env_ids),
    column_titles=env_ids,
    horizontal_spacing=0.1,
    vertical_spacing=0.05,
)

for col, env_id in enumerate(env_ids, 1):
    records = []
    for test_dir in results_dir.glob(f"{env_id}*"):
        with open(test_dir / "config.yml", "r") as f:
            cfg = yaml.load(f)

        record = {}
        df = scalars.read(test_dir)
        df_ = df[df["tag"] == "val/mean_ep_ret"]
        record["score"] = df_.loc[df_["step"].idxmax(), "value"]
        df_ = df[df["tag"] == "val/wm_loss"]
        record["val/wm_loss"] = df_.loc[df_["step"].idxmax(), "value"]

        records.append(record)

    df = pd.DataFrame.from_records(records)
    fig_ = px.scatter(df, x="val/wm_loss", y="score")
    for trace in fig_.data:
        fig.add_trace(trace, row=1, col=col)

fig